In [6]:
import sys
sys.path.append('..')

import os
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
import imageio  # for saving .gif
from IPython.display import HTML

import tifffile

def create_timelapse(data_dir, output_gif=None, fps=5, z=None):
    """
    Create a timelapse animation from a directory of TIFF files.
    
    Args:
        data_dir (str): Path to directory containing TIFF files
        output_gif (str): Path for output GIF file
        fps (int): Frames per second for animation and GIF
    """

    tiff_files = sorted(f for f in os.listdir(data_dir) if f.endswith('.tif'))
    
    frames = []
    for fname in tiff_files:
        path = os.path.join(data_dir, fname)
        img = tifffile.imread(path)
        frames.append(img)

    # Create stack and perform MIP or select Z-slice
    stack = np.stack(frames, axis=0)
    print("original video shape: ", stack.shape)
    if z is None:
        data_2d = stack.max(axis=1)  # MIP along Z-axis if 3D
    else:
        data_2d = stack[:, z, ...]  # Select Z-slice

    print("data_2d shape: ", data_2d.shape)
    
    
    fig, ax = plt.subplots(figsize=(8, 8)) 
    im = ax.imshow(data_2d[0], cmap='gray', animated=True)
    ax.set_title("Time-lapse")
    plt.close()  # Prevent display of empty figure
    
    def update(frame_idx):
        im.set_data(data_2d[frame_idx])
        return [im]
    
    interval = 1000 // fps  # Convert fps to milliseconds interval
    ani = animation.FuncAnimation(fig, update, frames=range(data_2d.shape[0]),
                                interval=interval, blit=True)
    
    # Save as GIF if output_gif is specified
    if output_gif:
        gif_frames = []
        for i in range(data_2d.shape[0]):
            frame_8bit = (data_2d[i] / data_2d[i].max() * 255).astype(np.uint8)
            gif_frames.append(frame_8bit)
        
        imageio.mimsave(output_gif, gif_frames, fps=fps)
        print(f"Wrote {output_gif}")
    
    return HTML(ani.to_jshtml())  # Return HTML directly


In [7]:
cell = "cell0006_R0007"
video_types = ["raw", "conc", "mask"]
video_type = "conc"
data_path = f"../data/mitotic_cell_atlas_v1.0.1_exampledata/Data_tifs/161122_gfpBUBR1cM04-A03_MitoSys1/{cell}/{video_type}tif"
display(create_timelapse(data_path, fps=10))

original video shape:  (40, 31, 256, 256)
data_2d shape:  (40, 256, 256)
